In [1]:
# 라이브러리 import
# !pip install pandas-profiling[notebook]
import requests
import json
import pandas as pd
import numpy as np
from pandas_profiling import ProfileReport

/tmp/ipykernel_56372/1523786740.py:7: DeprecationWarning: `import pandas_profiling` is going to be deprecated by April 1st. Please use `import ydata_profiling` instead.
  from pandas_profiling import ProfileReport


In [2]:
#id정보 불러오기
url_id = 'http://www.smartfarmkorea.net/Agree_WS/webservices/ProvideRestService/getIdentityDataList/fc918c3668964be490f67fe52bbef49c'
response = requests.get(url_id)
contents = response.text
js = json.loads(contents)

In [3]:
js = json.loads(contents)
print(type(js)) #json타입 확인

<class 'list'>


In [4]:
#df으로
js = json.loads(contents)
df_id = pd.DataFrame(js)
df_id

statusCode statusMessage       userId      facilityId  addressName  \
0           00   NORMAL_CODE  PFS_0000001  PFS_0000001_01     경상남도 사천시   
1         None          None  PFS_0000002  PFS_0000002_01     전라북도 김제시   
2         None          None  PFS_0000003  PFS_0000003_01     경상남도 함안군   
3         None          None  PFS_0000004  PFS_0000004_01     경상남도 진주시   
4         None          None  PFS_0000005  PFS_0000005_01     경상남도 진주시   
..         ...           ...          ...             ...          ...   
535       None          None       sk0085       sk0085_01  세종특별자치시 연동면   
536       None          None       sk0091       sk0091_01  세종특별자치시 연동면   
537       None          None       sk0102       sk0102_01  세종특별자치시 연동면   
538       None          None       sk0104       sk0104_01  세종특별자치시 연동면   
539       None          None       sk0118       sk0118_01  세종특별자치시 연동면   

    itemCode  
0     080300  
1     080300  
2     080300  
3     080300  
4     132600  
..       ...  
535   080300  
536   080300  
537   080300  
538   080300  
539   080300  

[540 rows x 6 columns]

In [5]:
#fast EDA
profile = ProfileReport(df_id, title="Report")
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

ID set
- 총 892농가
- userid facilityId 1:1매칭 
- addressname 결측값 86개 
- itmecode 토마토(080300):151농가, 딸기(080400):293농가, 방토(080600):1농가 

In [6]:
# df_item_list=['080400'] #딸기 농가만 남기기 294농가
# raw_id=df_id[df_id['itemCode'].isin(df_item_list)]
# print(len(df_id[(df_id['itemCode'].isin(df_item_list))&(df_id['addressName']=='null')])) #딸기 농가중엔 지역코드 결측 없음

raw_id=df_id
raw_id

statusCode statusMessage       userId      facilityId  addressName  \
0           00   NORMAL_CODE  PFS_0000001  PFS_0000001_01     경상남도 사천시   
1         None          None  PFS_0000002  PFS_0000002_01     전라북도 김제시   
2         None          None  PFS_0000003  PFS_0000003_01     경상남도 함안군   
3         None          None  PFS_0000004  PFS_0000004_01     경상남도 진주시   
4         None          None  PFS_0000005  PFS_0000005_01     경상남도 진주시   
..         ...           ...          ...             ...          ...   
535       None          None       sk0085       sk0085_01  세종특별자치시 연동면   
536       None          None       sk0091       sk0091_01  세종특별자치시 연동면   
537       None          None       sk0102       sk0102_01  세종특별자치시 연동면   
538       None          None       sk0104       sk0104_01  세종특별자치시 연동면   
539       None          None       sk0118       sk0118_01  세종특별자치시 연동면   

    itemCode  
0     080300  
1     080300  
2     080300  
3     080300  
4     132600  
..       ...  
535   080300  
536   080300  
537   080300  
538   080300  
539   080300  

[540 rows x 6 columns]

In [7]:
#딸기농가 아이디로 작기table 불러오기

df_id_list=list(raw_id['userId']) 
#df_id_list=['PFS_0000001','PFS_0000002','PFS_0000003']
url_crop= 'http://www.smartfarmkorea.net/Agree_WS/webservices/ProvideRestService/getCroppingSeasonDataList/fc918c3668964be490f67fe52bbef49c/'
list_df_cropping =[]
for i in df_id_list:
    # print(url_cropping)
    df_crop = pd.DataFrame(json.loads(requests.get(url_crop+i).text))
    df_crop['userId']=i
    list_df_cropping.append(df_crop)
df_cropping = pd.concat(list_df_cropping,ignore_index=True)
df_cropping

/tmp/ipykernel_56372/4276888679.py:12: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  df_cropping = pd.concat(list_df_cropping,ignore_index=True)


statusCode statusMessage croppingSerlNo croppingSeasonName itemCode  \
0            00   NORMAL_CODE             79      데프니스_20150902   080300   
1          None          None           4940          2021년 토마토   080300   
2          None          None           5957          2022년_토마토   080300   
3            00   NORMAL_CODE             80        다볼_20150714   080300   
4            00   NORMAL_CODE             81      데프니스_20150902   080300   
...         ...           ...            ...                ...      ...   
1280         00   NORMAL_CODE             44      마미리오_20160211   080300   
1281       None          None            203       슈퍼탑_20160720   080300   
1282         00   NORMAL_CODE            325            토마토_레드찰   080300   
1283       None          None            326           티티찰_2016   080300   
1284         00   NORMAL_CODE             47       244_20160202   080300   

     croppingDate croppingEndDate        croppingSystem  cultivationArea  \
0      2015-09-02      2016-12-31  B0004000000000000002           1180.0   
1      2021-09-13      2022-07-30                  None           1785.0   
2      2022-09-21      2023-07-25                  None           1785.0   
3      2015-07-14      2016-12-31  B0004000000000000002           3400.0   
4      2015-09-02      2016-12-31  B0004000000000000002           1500.0   
...           ...             ...                   ...              ...   
1280   2016-02-11      2016-12-31  B0004000000000000001           3000.0   
1281   2016-07-20      2016-12-31  B0004000000000000001           3000.0   
1282   2016-02-11      2016-12-31  B0004000000000000002           1500.0   
1283   2016-07-20      2016-12-31  B0004000000000000002              NaN   
1284   2016-02-02      2016-12-31  B0004000000000000001           3000.0   

      calCultivationArea  ...  planSlabNum  plantDensity  \
0                 3894.0  ...          4.0           2.5   
1                 5900.0  ...          NaN           NaN   
2                 5900.0  ...          NaN           NaN   
3                11220.0  ...          4.0           2.5   
4                 4950.0  ...          4.0           2.5   
...                  ...  ...          ...           ...   
1280              9900.0  ...          5.0           2.5   
1281              9900.0  ...          5.0           2.5   
1282                 NaN  ...          NaN           NaN   
1283                 NaN  ...          NaN           NaN   
1284              9900.0  ...          5.0           2.5   

      standardPlantDensity  floodlightDec  leafArea  stndTemp  stndWeight  \
0                      2.5            0.8       0.0      20.0       180.0   
1                      NaN            NaN       NaN       NaN         NaN   
2                      NaN            NaN       NaN       NaN         NaN   
3                      2.5            0.7       0.0      20.0       180.0   
4                      2.5            0.7       0.0      18.0       180.0   
...                    ...            ...       ...       ...         ...   
1280                   2.5            0.7       0.0      18.0       180.0   
1281                   2.5            0.7       2.5      18.0       180.0   
1282                   NaN            0.7       NaN      18.0        80.0   
1283                   NaN            NaN       NaN       NaN        80.0   
1284                   2.5            0.7       0.0      18.0       180.0   

      stndSolar  stndMeta       userId  
0         150.0     130.0  PFS_0000001  
1           NaN       NaN  PFS_0000001  
2           NaN       NaN  PFS_0000001  
3         150.0     150.0  PFS_0000002  
4         100.0     130.0  PFS_0000003  
...         ...       ...          ...  
1280      100.0     130.0       sk0102  
1281      100.0     130.0       sk0102  
1282      100.0       NaN       sk0104  
1283        NaN       NaN       sk0104  
1284      100.0     130.0       sk0118  

[1285 rows x 23 columns]

In [9]:
raw_id.to_excel(excel_writer='raw_id.xlsx')
df_cropping.to_excel(excel_writer='df_cropping.xlsx')

In [10]:
profile = ProfileReport(df_cropping, title="Report")
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

작기정보 set
- croppingSerlNo, 작기 번호가 없는 데이터 105개
- 